In [1]:
import torch
import torch.nn as nn
import torch.optim as optim
from pytorch_tabular.models import GANDALFConfig
from torch.utils.data import DataLoader, TensorDataset,random_split
import numpy as np
import pandas as pd
from pytorch_tabular import TabularModel
from pytorch_tabular.config import DataConfig, OptimizerConfig, TrainerConfig, ExperimentConfig
from pytorch_tabular.models import CategoryEmbeddingModelConfig

from sklearn.preprocessing import OrdinalEncoder
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split


In [2]:
riot_data = pd.read_csv("reshape_total_riot.csv", nrows=1000)
riot_data = riot_data.drop(columns=['win', 'win.1', 'win.2', 'win.3', 'win.4', 'win.5', 'win.6', 'win.7', 'win.8', 'win.9'])



In [3]:
loaded_model = TabularModel.load_model("model.pth")

2024-05-27 23:54:33,819 - {pytorch_tabular.tabular_model:165} - INFO - Experiment Tracking is turned off

2024-05-27 23:54:33,830 - {pytorch_tabular.tabular_model:340} - INFO - Preparing the Trainer

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.rich_model_summary.RichModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


In [4]:
# soft_targets = loaded_model.predict(riot_data)
# print(soft_targets)

# 교사 모델의 예측 확률 생성
teacher_predictions = loaded_model.predict(riot_data)

c:\Users\a\AppData\Local\pypoetry\Cache\virtualenvs\tabulr_transformers-5PYuSfOC-py3.11\Lib\site-packages\pytorch_tabular\categorical_encoders.py:67: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  X_encoded[col].fillna(self._imputed, inplace=True)
c:\Users\a\AppData\Local\pypoetry\Cache\virtualenvs\tabulr_transformers-5PYuSfOC-py3.11\Lib\site-packages\pytorch_tabular\categorical_encoders.py:67: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The b

In [5]:
patterns = ['teamId', 'championId','perk','primaryStyle', 'subStyle', 'tier']
selected_columns = [col for col in riot_data.columns if any(pattern in col for pattern in patterns)]
riot_data = riot_data[selected_columns]


categorical_columns = [ col for col in riot_data.columns if riot_data[col].dtype == "object"]
numerical_columns = [ col for col in riot_data.columns if riot_data[col].dtype != "object"]


encoder = OrdinalEncoder()
riot_data[categorical_columns] = encoder.fit_transform(riot_data[categorical_columns])

# 수치형 데이터 스케일링
scaler = StandardScaler()
riot_data[numerical_columns] = scaler.fit_transform(riot_data[numerical_columns])
print(riot_data.head())

   championId  tier  teamId     perk1     perk2     perk3     perk4  \
0   -0.644152   4.0     0.0  0.079077 -0.541304 -1.020131  0.335103   
1   -0.712617   4.0     0.0  0.079077 -0.541304 -1.020131  0.335103   
2   -0.502333   4.0     0.0 -0.542233  1.503070  1.052618 -1.290300   
3   -0.487662   1.0     0.0 -0.547907  1.503070  1.052618 -1.290300   
4   -0.296940   4.0     0.0 -0.556418  1.503070  1.054936  0.787008   

   primaryStyle     perk5     perk6  ...  tier.9  teamId.9   perk1.9  \
0      0.586868  0.179120  0.121259  ...     4.0       0.0  0.080830   
1      0.586868 -0.914233 -0.863792  ...     4.0       0.0  0.593608   
2     -0.874821  0.189105 -0.078539  ...     4.0       0.0  0.080830   
3     -0.874821 -0.869301 -0.845206  ...     1.0       0.0  5.734614   
4     -0.874821 -0.385030 -0.403792  ...     4.0       0.0  0.130454   

    perk2.9   perk3.9   perk4.9  primaryStyle.9   perk5.9   perk6.9  \
0 -0.543764 -1.019400  0.281761        0.524231  0.121170 -0.003137  

In [6]:

# 소프트 타겟을 DataFrame으로 변환
soft_targets = pd.DataFrame(teacher_predictions)
# # 원래의 훈련 데이터에 소프트 타겟 추가
# train_data_with_soft_targets = pd.concat([riot_data.reset_index(drop=True), soft_targets], axis=1)


In [7]:
# train_data_with_soft_targets.head()

In [8]:
# # 데이터 설정 업데이트 (소프트 타겟 포함)
# data_config_student = DataConfig(
#     target=["0_probability", "1_probability", "prediction"],  # 원래 타겟과 소프트 타겟 모두 포함
#     continuous_cols=numerical_columns,  # 연속형 변수에 소프트 타겟 추가
#     categorical_cols=categorical_columns  # 범주형 변수
# )

# model_config = GANDALFConfig(
#     task="classification",
#     gflu_stages=6,
#     gflu_feature_init_sparsity=0.3,
#     gflu_dropout=0.0,
#     learning_rate=1e-3,
# )
# trainer_config = TrainerConfig(
#     auto_lr_find=True,  # Learning rate 자동 탐색
#     batch_size=128,
#     max_epochs=100,
#     min_epochs=5,
# )

# # 학생 모델 구성 (데이터 설정 업데이트 적용)
# student_model_with_soft_target = TabularModel(
#     data_config=data_config_student,
#     model_config=model_config,
#     optimizer_config=OptimizerConfig(),
#     trainer_config=trainer_config,
#     verbose=True
# )


In [9]:
# Transformer Encoder Layer
class TransformerEncoder(nn.Module):
    def __init__(self, embed_dim, num_heads, ff_dim):
        super(TransformerEncoder, self).__init__()
        self.attention = nn.MultiheadAttention(embed_dim, num_heads)
        self.feed_forward = nn.Sequential(
            nn.Linear(embed_dim, ff_dim),
            nn.ReLU(),
            nn.Linear(ff_dim, embed_dim)
        )
        self.norm1 = nn.LayerNorm(embed_dim)
        self.norm2 = nn.LayerNorm(embed_dim)
        self.dropout = nn.Dropout(0.1)

    def forward(self, src):
        src2 = self.norm1(src)
        attn_output, _ = self.attention(src2, src2, src2)
        src = src + self.dropout(attn_output)
        src2 = self.norm2(src)
        ff_output = self.feed_forward(src2)
        src = src + self.dropout(ff_output)
        return src

In [10]:
class TabTransformer(nn.Module):
    def __init__(self, num_features, num_targets, embed_dim, num_heads, ff_dim, num_layers):
        super(TabTransformer, self).__init__()
        self.embeddings = nn.ModuleList([nn.Embedding(10, embed_dim) for _ in range(num_features)])  # 범주 수 10 가정
        self.encoder_layers = nn.ModuleList([TransformerEncoder(embed_dim, num_heads, ff_dim) for _ in range(num_layers)])
        self.classifier = nn.Linear(embed_dim, num_targets)  # 여러 타깃 출력

    def forward(self, x):
        x = torch.cat([emb(x[:, i]) for i, emb in enumerate(self.embeddings)], dim=1)
        x = x.unsqueeze(1)  # 시퀀스 차원 추가
        for layer in self.encoder_layers:
            x = layer(x)
        x = x.squeeze(1)
        return self.classifier(x)  # 활성화 함수 적용 없음


In [11]:
riot_data.head()

championId  tier  teamId     perk1     perk2     perk3     perk4  \
0   -0.644152   4.0     0.0  0.079077 -0.541304 -1.020131  0.335103   
1   -0.712617   4.0     0.0  0.079077 -0.541304 -1.020131  0.335103   
2   -0.502333   4.0     0.0 -0.542233  1.503070  1.052618 -1.290300   
3   -0.487662   1.0     0.0 -0.547907  1.503070  1.052618 -1.290300   
4   -0.296940   4.0     0.0 -0.556418  1.503070  1.054936  0.787008   

   primaryStyle     perk5     perk6  ...  tier.9  teamId.9   perk1.9  \
0      0.586868  0.179120  0.121259  ...     4.0       0.0  0.080830   
1      0.586868 -0.914233 -0.863792  ...     4.0       0.0  0.593608   
2     -0.874821  0.189105 -0.078539  ...     4.0       0.0  0.080830   
3     -0.874821 -0.869301 -0.845206  ...     1.0       0.0  5.734614   
4     -0.874821 -0.385030 -0.403792  ...     4.0       0.0  0.130454   

    perk2.9   perk3.9   perk4.9  primaryStyle.9   perk5.9   perk6.9  \
0 -0.543764 -1.019400  0.281761        0.524231  0.121170 -0.003137   
1 -0.360517 -0.759025  1.088574        1.242356 -0.863758 -0.872654   
2 -0.543764 -1.019400  0.281761        0.524231  0.714954  0.613940   
3 -0.778696 -1.188293 -0.679080       -0.193894  0.587715  0.707436   
4 -0.543764 -1.019400  0.281761        0.524231  0.111745  0.118409   

   subStyle.9  
0    0.496589  
1   -1.153209  
2    1.321489  
3    1.321489  
4    0.496589  

[5 rows x 110 columns]

In [47]:
# 손실 함수 설정
criterion = nn.BCEWithLogitsLoss()  # Binary Cross-Entropy with Logits 손실 함수

model = TabTransformer(
    num_features=110,
    num_targets=3,
    embed_dim=64,
    num_heads=2,
    ff_dim=256,
    num_layers=3
)

categorical_tensor = torch.tensor(riot_data[categorical_columns].values, dtype=torch.long)
numerical_tensor = torch.tensor(riot_data[numerical_columns].values, dtype=torch.float32)
target = torch.tensor(soft_targets.values, dtype=torch.float32)

inputs = torch.cat((categorical_tensor, numerical_tensor), dim=1)
dataset = TensorDataset(inputs, target)

train_size = int(0.8 * len(dataset))
test_size = len(dataset) - train_size
train_dataset, test_dataset = random_split(dataset, [train_size, test_size])


train_loader = DataLoader(train_dataset, batch_size=8, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=8, shuffle=False)



# outputs = model(x_tensor)
# y_tensor = torch.tensor(soft_targets.values, dtype=torch.float32)
# loss = criterion(outputs, y_tensor)
# print("Loss:", loss.item())
# outputs.save("model.pth")

In [50]:
def train(model, train_loader, criterion, optimizer, epochs=10):
    model.train()
    for epoch in range(epochs):
        total_loss = 0
        for batch in train_loader:
            inputs, labels = batch
            # 범주형 데이터가 포함되어 있다면, 범주형 데이터를 torch.long으로 변환
            if isinstance(inputs, list):  # 입력 데이터가 리스트로 구성된 경우
                categorical_inputs = inputs[0].long()  # 범주형 데이터를 torch.long으로 변환
                numerical_inputs = inputs[1]  # 수치형 데이터
                inputs = torch.cat((categorical_inputs, numerical_inputs), dim=1)
            optimizer.zero_grad()
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()
            total_loss += loss.item()
        print(f'Epoch {epoch+1}, Average Loss: {total_loss / len(train_loader)}')


In [51]:
optimizer = optim.Adam(model.parameters(), lr=0.001)
# print(train_loader.dataset.tensors[0].shape)
train(model, train_loader, criterion, optimizer)


RuntimeError: Expected tensor for argument #1 'indices' to have one of the following scalar types: Long, Int; but got torch.FloatTensor instead (while checking arguments for embedding)

In [ ]:
# student_model_with_soft_target.fit(train=train_df, validation=valid_df)
# student_model_with_soft_target.save_model("student_model.pth")  # 학습된 모델 저장